# Quantum circuits and simulation of noisy algorithms

Welcome to this hands-on session. The session is build around interactive Notebooks, that include code, explanations and tasks. Please run the code cells on your computer and follow the instructions of the tasks to deepen your learning.    

Jami Rönkkö, IQM Quantum Computers, email: jami@meetiqm.com

# Quantum Phase Estimation algorithm

In this notebook you will learn:
- What is the Quantum Phase Estimation algorithm 
- How it works and how to implement it

In an earlier notebook we learned about Quantum Fourier Transformation and how it transforms states expressed in *computational basis* into *Fourier basis*.

As the name suggests, the goal of Quantum Phase Estimation is to estimate the phase of an eigenvalue of a unitary operator. In mathematical terms, given some statevector $|\psi$⟩ and unitary operator $U$ (for example some quantum gate) whose eigenstate is $|\psi$⟩, the QPE algorithm finds the phase $\theta$ appearing in the eigenvalue equation:
$$
U∣\hspace{-0.1cm}\psi⟩=e^{2\pi i \theta}∣\hspace{-0.1cm}\psi⟩
$$

To make this immediately more concrete, let us take as an example single-qubit state $|\psi$⟩ = ∣1⟩ that is an eigenstate of the phase gate $U=P(\phi)$, since
$$
P(\phi)∣\hspace{-0.1cm}1⟩=e^{i\phi}∣\hspace{-0.1cm}1⟩
$$
We can then use QPE to find $\phi$. Note that knowing the phase $\theta$ in the eigenvalue $e^{2\pi i \theta}$, means that we know the eigenvalue itself. Finding eigenvalues (especially eigenenergies for ground states) is important in computational chemistry. 

## Intuition behind QPE
QPE utilises the *symmetry of two-qubit phase gates*: either qubit can be though of as the control or target (**phase kickback**). Because of this, we can write the phase produced by unitary operator (gate) to a target qubit(s) into a separate register of 'counting qubits'. This is done by setting the counting qubit register into **Fourier basis** and changing the phases of their states based on the phase the unitary operator $U$ adds to the target qubit.

Specifically, the nearest integer $k$ to $2^n\theta$ will be encoded in the Fourier state ($n$ is the number of counting qubits). If $2^n\theta$ happens to be integer, we obtain the exact phase by reading out $k$ and solving $\theta = k / 2^n$. (Otherwise QPE will give approximate $\theta$ if one repeats QPE many times and considers the mean of the outcome as estimate for $\theta$.)

From the Quantum Fourier Transform notebook we remember that reading out integer from a Fourier basis state requires application of **inverse Quantum Fourier Transform**; after which the integer can be read as a binary string from the measured computational basis state. This trick will conclude QPE algorithm.

To express this in algorithmic steps:

**Algorithm**: Quantum Phase Estimation

**Goal**:\
 Figure out the phase $\theta$ caused by (in general unknown) gate $U$ to (in general unknown) target qubit(s) state ∣$\psi$⟩, given that ∣$\psi$⟩ is eigenstate of $U$ with eigenvalue $e^{2\pi i\theta}$ 
 
**Procedure**:
1) Initalize the $n$ qubit counting register to Fourier basis by applying Hadamard gate to each (bigger $n$ yields in general better estimate for $\theta$)
2) Apply the controlled-$U$ gate $2^j$ times to $j\text{'th}$ counting qubit and target qubit for $j$ between $0$ and $n$-1
3) Apply the inverse QFT to the counting qubit register
4) Read out the counting qubit register to obtain estimation for $2^n\theta$ in binary format (this is exact if $2^n\theta$ is integer)
5) In general, repeat many times to obtain most probable state as the solution (if $2^n\theta$ is integer, the phase is exact and one measurement is enough in ideal case)


# Circuit for Quantum Phase Estimation Algorithm

### GOAL: Using QPE, find out phase produced by single-qubit phase gate P($\pi/4$).

We follow the steps displayed above with $U=P(\pi/4)$. **In this case we know the answer ahead of time**: 

Since $\theta$ is defined as the number multiplying $2\pi i$ in the eigenvalue $e^{2\pi i \theta}$ of the state ∣1⟩ and the phase gate $P(\pi/4)$ adds phase $e^{i\pi/4}$ to ∣1⟩, we see that now $\theta=1/8$.   
 
Finally we note that, for three counting qubits $n=3$ and $\theta=1/8$, the number stored in our qubit register will be $2^n\theta=8/8=1$. This means that we can solve $\theta$ with 100% accuracy with one measurement (in absence of noise). If $\theta$ would be $1/4$, we would need only two counting qubits to have integer valued $2^n\theta$. You'll find the general case of non-integer $2^n\theta$ here: https://qiskit.org/textbook/ch-algorithms/quantum-phase-estimation.html

Let us now go ahead and create the circuit that implements QPE.

<font color='#5ACA97'><h2>TASK 1</h2></font>
> Write a code snippet that creates a `statevector_simulator`, executes the `QPE_circuit` and views the statevector. Hint: you get this from the previous notebooks
>
> Read and execute all the cells below. As you do this, paste the aforementioned code snippet to the cells reading 'Simulate the circuit and view statevector here'. 
>
> In this way we can see how the statevector of the QPU looks at each stage of the algorithm. This is valuable insight to algorithms that can be only obtained through simulators (or pen and paper) as opposed to running real QPU's.

In [ ]:
# Import everything from qiskit 
from qiskit import *
import numpy as np

## 1)

In [ ]:
# Create a circuit with 3 counting qubits and one qubit for the eigenstate of phase gate
QPE_circuit = QuantumCircuit(4, 3)     # Only the counting qubits need be measured -> add 3 classical qubits for storing measurement outcome
QPE_circuit.x(3)                       # Set the last qubit to |1> i.e. eigenstate

# Apply Hadamard gates to the counting qubits to transform the register to the Fourier basis: |000> -> |+++> (equal superposition of all computational states) 
QPE_circuit.h([0,1,2])

QPE_circuit.draw(output='mpl')

In [ ]:
# Simulate the circuit and view statevector here

## 2)

Then comes the main part of QPE, we perform controlled phase gates to encode number $2^n\theta$ to the counting qubits in the Fourier basis. This is essentially same thing we do in Quantum Fourier Transform:
1) first qubit gets phase-rotated $\pi/4$ radians (since our target gate is P($\pi/4$))
2) second qubit gets rotated twice that much (we apply two $\pi/4$ phase-rotations)
3) third qubit gets rotated again twice that much (four $\pi/4$ phase-rotations)
4) we would continue like this if there would be more counting qubits 


In [ ]:
repetitions = 1
for counting_qubit in range(3):                      # Loop over all counting qubits
    for i in range(repetitions):                     # Each qubit will be phase-rotated different multiple of pi/4 to encode this phase in the Fourier state of the register
        QPE_circuit.cp(np.pi/4, counting_qubit, 3)   # Apply conditional P(pi/4) gate to target qubit and counting qubit
    repetitions *= 2                                 # Increment repetitions such that each qubit gets phase-rotated double twice as much as previous 
QPE_circuit.draw(output='mpl')

In [ ]:
# Simulate the circuit and view statevector here

## 3) 

Final step of QPE circuit transforms the counting qubit register from Fourier basis back to computational basis. This is done by the inverse Quantum Fourier Transform. Let's recreate the inverse QFT function of previous notebook here:

In [ ]:
# Function that applies n qubit QFT to a circuit
def QFT(circuit, n):
    for i in range(n):
        circuit.barrier()                          # For sake of clarity, insert visual barriers between the QFT segments
        circuit.h(i)                               # Apply Hadamard to each qubit
        for j in range(i+1, n):               
            circuit.cp(np.pi / 2**(j-i), i, j)     # Apply controlled P gate with angle pi/2^(j-i) from qubit i to all qubits with higher index j
    return circuit

# Function that applies n-qubit inverse QFT to a circuit
def inverse_QFT(circuit, n):
    qft_circuit = QFT(QuantumCircuit(n, name ="QFT"), n)     # Create a QFT circuit
    inverse_qft_circuit = qft_circuit.inverse()              # Create an inverse of the circuit
    circuit.append(inverse_qft_circuit, circuit.qubits[:n])  # Add the gates of inverse QFT to the first n qubits of the targer circuit
    return circuit

In [ ]:
# Apply inverse QFT
QPE_circuit = inverse_QFT(QPE_circuit, 3)
# Measure
QPE_circuit.barrier()
QPE_circuit.measure([0,1,2],[0,1,2])

QPE_circuit.draw(output='mpl')

> Note: the inverse QFT circuit is here truncated to a single box for the printout. This is good way of visualizing circuits with known subroutines.

In [ ]:
# Simulate the circuit and view statevector here

We then measure the counting register:

In [ ]:
simulator = Aer.get_backend('qasm_simulator')                              # We use another simulator for measurement simulations
result = execute(QPE_circuit, backend = simulator, shots = 1).result()     # Single shot should suffice to give right answer with 100%

from qiskit.visualization import plot_histogram
plot_histogram(result.get_counts())

We have now succesfully executed the Quantum Phase Estimation algorithm and read out binary representation for $8\theta$ from the three counting qubits. The reason for this extra factor of 8 is that the application of controlled P($2\pi\theta$) gates in the Fourier basis differs a bit from Quantum Fourier Transform. Hence, when we apply the inverse QFT we obtain $2^n\theta$ instead of just $\theta$ in the computational basis. 

<font color='#5ACA97'><h2>TASK 2</h2></font>
> We read bitstring $100$ from our qubits. Confirm that this is always the case by increasing `shots` in the cell above.
>
> Solve $\theta$ from the equation $2^n \theta = k$, where $n$ is the number of counting qubits and $k$ is the number we read out from the counting register in decimal format. 
>
> Note: QFT inverts the qubit order. Hence you should read the bitstring $100$ in opposite order as $001$  
>
> Did we get the correct phase $\phi=\pi/4$? See 'Interpreting the result' below.

### Interpreting the result
Once we have figured out $\theta$, we obtain the phase $e^{i\pi/4}$ added by P($\phi=\pi/4$) to ∣1⟩ gate by inserting $\theta$ to the eigenvalue defined as $e^{2\pi i\theta}$.

<font color='#5ACA97'><h2>EXTRA TASK</h2></font>
> You can try the QPE for phase gate P($\phi$) with different angle $\phi$. 
> Remember that if $2^n \theta$ is not integer, you will not get exact result and will have to run the circuit multiple times for estimate. 
>
> For guidance, see: https://qiskit.org/textbook/ch-algorithms/quantum-phase-estimation.html

## Takeaway

- Quantum Phase Estimation is a useful application of the Quantum Fourier Transform for finding phase or eigenvalue of a unitary operator (gate)
 
- It is used also in Shor's algorithm and for finding ground states of molecules

In the last notebook we will discover the effect of noise on quantum computers and simulate noisy execution of QPE algorithm on the Helmi QPU.  